In [1]:
import os
import re
import pandas as pd
import numpy as np
from natsort import natsorted, index_natsorted, order_by_index
from tools import * # функции для обработки
pd.set_option('display.max_columns', 50)
pd.set_option('display.max_rows', 1000)

### Обработка файлов формы № 10.3

In [2]:
year = 2020

Первый лист .xls-файла мы пропускаем, так как во всех отчетных формах там содержится общая информация, а не данные.

In [3]:
mailFile = 'ExcelFiles/Main/' + str(year) + 'main.xls'
mainDF = pd.read_excel(mailFile, 1, header=0)

Удаляем строку "Всего по составам УК РФ" значения сохраняем в отдельную переменную - они будут нужны позже, для проверки корректности обработки данных.

In [4]:
mainDF['clause'] = mainDF['clause'].astype('str')
total_values = list(mainDF[mainDF['clause'].str.contains("Всего по составам УК РФ|Всего лиц по составам УК РФ")].values[0][1:])
mainDF = mainDF[~mainDF['clause'].str.contains('Всего по составам УК РФ')]

In [5]:
mainDF = cleanClauseCol(mainDF) # чистим колонку с номерами статей от лишнего текста
mainDF = clauses2column(mainDF) # используя регулярное выражение, создаем колонки со номерами статей и частей 
firstCols = ['clause', 'part', 'totalConvicted']
mainDF = rearrangeCols(mainDF, firstCols) # меняем порядок столбцов для удобства

# поскольку названия частей вместе с примечаниями мы берем из формы 10-а, в тех случаях, где номера статей в формах 
# 10.3 и 10.3.1 и 10-а расходятся (в одной таблице - номер устаревшей статьи, а в друой - уже новой)
# - ориентируемся на 10-а

mainDF['part'] = mainDF['part'].replace('136ч.2', '136')
mainDF['part'] = mainDF['part'].replace('168$', '168ч.1', regex=True)

mainDF = sortTable(mainDF) # упорядочиваем строки

Выше мы сохранили значения строки "Всего по составам УК РФ", которая содержит сумммы по каждому столбцу. Теперь мы используем их для проверки корректности обработки данных, сравнив суммы по столбцам со значениями, указанными в строке "Всего по составам УК РФ".

К сожалению, как показала практика, числа эти не всегда совпадают, поэтому каждое несовпадение мы перепроверили вручную. Кроме того, еще в одном случае суммы действительно не совпадают из-за удаления в файлах 2011 год строки "Преступления, введенные в УК РФ после утверждения форм отчетности приказом № 115 от 10.06.2011" с одним осужденным к ограничению свободы (см. выше).

In [6]:
# выводит несоответствия сумм, если ничего не печатает - несоответствий нет
compareSums(mainDF, mainDF.columns, total_values, 2)

In [7]:
mainDF

clause                   part  totalConvicted  \
0                      105                 105ч.1            4027   
1                      105                 105ч.2             987   
2                      106                    106              29   
3                      107                 107ч.1              37   
4                      107                 107ч.2               1   
5                      108                 108ч.1             227   
6                      108                 108ч.2               0   
7                      109                 109ч.1             772   
8                      109                 109ч.2             114   
9                      109                 109ч.3              39   
10                   110.1               110.1ч.1               0   
11                   110.1               110.1ч.2               0   
12                   110.1               110.1ч.3               1   
13                   110.1               110.1ч.4               1   
14                   110.1               110.1ч.5               0   
15                   110.1               110.1ч.6               0   
16                   110.2               110.2ч.1               0   
17                   110.2               110.2ч.2               0   
18                     110                 110ч.1               5   
19                     110                 110ч.2               1   
20                     111                 111ч.1            3183   
21                     111                 111ч.2            9148   
22                     111                 111ч.3             518   
23                     111                 111ч.4            3414   
24                     112                 112ч.1            5349   
25                     112                 112ч.2            2497   
26                     113                    113              10   
27                     114                 114ч.1             421   
28                     114                 114ч.2               4   
29                     115                 115ч.1            1620   
30                     115                 115ч.2            9294   
31                     116                    116             556   
32                   116.1                  116.1            1629   
33                     116                 116ч.1              50   
34                     116                 116ч.2               1   
35                     117                 117ч.1             931   
36                     117                 117ч.2             366   
37                     118                 118ч.1             811   
38                     118                 118ч.2              30   
39                     118                 118ч.3               0   
40                     118                 118ч.4               0   
41                     119                 119ч.1           16725   
42                     119                 119ч.2              14   
43                     120                 120ч.1               0   
44                     120                 120ч.2               0   
45                     121                 121ч.1               2   
46                     121                 121ч.2               0   
47                     122                 122ч.1              23   
48                     122                 122ч.2              30   
49                     122                 122ч.3              13   
50                     122                 122ч.4               0   
51                     123                 123ч.1               0   
52                     123                 123ч.2               0   
53                     123                 123ч.3               0   
54                   124.1               124.1ч.1               0   
55                   124.1               124.1ч.2               0   
56                     124                 124ч.1               0   
57                

### Обработка файлов формы № 10.3.1

In [8]:
parametersFile = 'ExcelFiles/MainParameters/' + str(year) + 'parameters.xls'
parametersDF = pd.read_excel(parametersFile, 1, header=0)

parametersDF['clause'] = parametersDF['clause'].astype('str')
total_values = list(parametersDF[parametersDF['clause'].str.contains("Всего по составам УК РФ|Всего лиц по составам УК РФ")].values[0][1:])
parametersDF = parametersDF[~parametersDF['clause'].str.contains('Всего по составам УК РФ')]
parametersDF = cleanClauseCol(parametersDF)
parametersDF = clauses2column(parametersDF)
parametersDF['part'] = parametersDF['part'].replace('136ч.2', '136')
parametersDF['part'] = parametersDF['part'].replace('168$', '168ч.1', regex=True)
firstCols = ['clause', 'part']
parametersDF = rearrangeCols(parametersDF, firstCols)
parametersDF = sortTable(parametersDF)

In [9]:
parametersDF

clause                   part  primaryImprisonment1  \
0                      105                 105ч.1                     1   
1                      105                 105ч.2                     1   
2                      106                    106                     2   
3                      107                 107ч.1                     0   
4                      107                 107ч.2                     1   
5                      108                 108ч.1                    14   
6                      108                 108ч.2                     0   
7                      109                 109ч.1                    74   
8                      109                 109ч.2                     2   
9                      109                 109ч.3                     1   
10                   110.1               110.1ч.1                     0   
11                   110.1               110.1ч.2                     0   
12                   110.1               110.1ч.3                     0   
13                   110.1               110.1ч.4                     0   
14                   110.1               110.1ч.5                     0   
15                   110.1               110.1ч.6                     0   
16                   110.2               110.2ч.1                     0   
17                   110.2               110.2ч.2                     0   
18                     110                 110ч.1                     0   
19                     110                 110ч.2                     0   
20                     111                 111ч.1                   111   
21                     111                 111ч.2                   351   
22                     111                 111ч.3                     4   
23                     111                 111ч.4                     3   
24                     112                 112ч.1                   530   
25                     112                 112ч.2                   159   
26                     113                    113                     1   
27                     114                 114ч.1                    53   
28                     114                 114ч.2                     0   
29                     115                 115ч.1                     1   
30                     115                 115ч.2                  1523   
31                     116                    116                    73   
32                   116.1                  116.1                     0   
33                     116                 116ч.1                     0   
34                     116                 116ч.2                     0   
35                     117                 117ч.1                   150   
36                     117                 117ч.2                     4   
37                     118                 118ч.1                     0   
38                     118                 118ч.2                     0   
39                     118                 118ч.3                     0   
40                     118                 118ч.4                     0   
41                     119                 119ч.1                  2790   
42                     119                 119ч.2                     3   
43                     120                 120ч.1                     0   
44                     120                 120ч.2                     0   
45                     121                 121ч.1                     0   
46                     121                 121ч.2                     0   
47                     122                 122ч.1                     9   
48                     122                 122ч.2                     1   
49                     122                 122ч.3                     0   
50                     122                 122ч.4                     0   
51                     123                 123ч.1                     0   
52                     123                 12

Снова проверяем суммы по столбцам. В двух столбцах они не сходятся: эта проблема есть и в исходных данных.

In [10]:
compareSums(parametersDF, parametersDF.columns, total_values, 2)


Сумма значений в колонке dismissalCourtFine5 17335 
 Значение в строке "Всего по составам УК РФ"  17336

Сумма значений в колонке dismissalCourtFine5_25 33155 
 Значение в строке "Всего по составам УК РФ"  33164


### Обработка файлов формы № 10-а 

In [11]:
addFile = 'ExcelFiles/Add/' + str(year) + 'add.xls'

columns = {
    'Число осужденных по основной статье': 'totalConvictedMain',
    'Виды преступлений': 'name',
    'Статьи Уголовного кодекса Российской Федерации по частям': 'clause',
    'Статьи УК РФ по частям': 'clause',
    'Дополнительная квалификация. Осуждено по числу лиц':  'addTotalPersons',
       'Дополнительная квалификация. Осуждено по количеству составов преступлений': 'addTotalOffences',
       'Дополнительная квалификация. Оправдано  по числу лиц': 'addAcquittalPersons',
       'Дополнительная квалификация. Оправдано  по количеству составов преступлений': 'addAcquittalOffences',
       'Дополнительная квалификация. Прекращено за отсутствием состава, события преступления, непричастностью к преступлению по числу лиц': 'addDismissalPersons',
       'Дополнительная квалификация. Прекращено за отсутствием состава, события преступления, непричастностью к преступлению по количеству составов преступлений': 'addDismissalOffences',
       'Дополнительная квалификация. Прекращено по иным основаниям по числу лиц': 'addDismissalOtherPersons',
       'Дополнительная квалификация. Прекращено по иным основаниям по количеству составов преступлений': 'addDismissalOtherOffences',
       'Принудительные меры медицинского характера в отношении невменяемого дополнительная квалификация по судебным постановлениям по количеству составов преступлений': 'addCoerciveMeasuresOffences',
    
}

df_list = pd.read_excel(addFile, sheet_name=None, header = None)
dfs = []
for key in list(df_list.keys())[2:-2]:
    df = df_list[key] # df_list[ 'Раздел 20 (Гл. 33)']
    df = dropFirstRows(df, 'Виды преступлений')
    df = dropFirstRows(df, '[а-яА-Я]{3,}', 1)
    df = deleteUnusedCols(df, year)
    df = tackleMergedCells(df)
    df.rename(columns=columns, inplace=True)
    df = df[df.columns[~df.columns.str.contains('[а-яА-Я]{2,}', regex=True)]]
    df.dropna(axis='rows', how='any', inplace=True)
    dfs.append(df)
addDF = pd.concat(dfs, ignore_index=True)
addDF['clause'] = addDF['clause'].astype('str')
addDF = addDF[~addDF['name'].str.contains('Виды преступлений')]

/home/kate/dostoevsky_data/venv/lib/python3.8/site-packages/pandas/core/frame.py:4147: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().fillna(
/home/kate/dostoevsky_data/venv/lib/python3.8/site-packages/pandas/core/frame.py:4166: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().replace(
/home/kate/dostoevsky_data/venv/lib/python3.8/site-packages/pandas/core/frame.py:4125: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-

In [12]:
addDF

0                                                 name  \
1                                             Убийство   
2              Убийство при отягчающих обстоятельствах   
3              Убийство матерью новорожденного ребенка   
4            Убийство, совершенное в состоянии аффекта   
5      Убийство в состоянии аффекта двух или более лиц   
6    Убийство при превышении пределов необходимой о...   
7    Убийство при превышении мер, необходимых для з...   
8                  Причинение смерти по неосторожности   
9    Причинение смерти по неосторожности при отягча...   
10   Причинение смерти по неосторожности двум или б...   
11                           Доведение до самоубийства   
12   Доведение до самоубийства, совершенное при отя...   
13   Склонение к совершению самоубийства или содейс...   
14         Содействие совершению самоубийства советами   
15   Деяния, предусмотренные частями первой или вто...   
16   Деяния, предусмотренные частью первой или втор...   
17   Деяния, предусмотренные частями первой или вто...   
18   Деяния, предусмотренные частями первой, второй...   
19   Организация деятельности, направленной на побу...   
20   Организация деятельности, направленной на побу...   
21        Умышленное причинение тяжкого вреда здоровью   
22   Умышленное причинение тяжкого вреда здоровью п...   
23   Умышленное причинение тяжкого вреда здоровью п...   
24   Умышленное причинение тяжкого вреда здоровью, ...   
25   Умышленное причинение средней тяжести вреда зд...   
26   Умышленное причинение средней тяжести вреда зд...   
27   Причинение тяжкого или средней тяжести вреда з...   
28   Причинение тяжкого вреда здоровью при превышен...   
29   Причинение тяжкого вреда здоровью при превышен...   
30   Умышленное причинение легкого вреда здоровью (...   
31   Умышленное причинение легкого вреда здоровью, ...   
32   Побои (включая ст. 116 УК РФ (до редакции ФЗ о...   
33        Побои, совершенные из хулиганских побуждений   
34                                              Побои    
35   Нанесение побоев лицом, подвергнутым администр...   
36                                           Истязание   
37            Истязание при отягчающих обстоятельствах   
38   Причинение тяжкого вреда здоровью по неосторож...   
39   Причинение тяжкого вреда здоровью по неосторож...   
40   Причинение средней тяжести вреда здоровью по н...   
41   Причинение тяжкого вреда здоровью по неосторож...   
42   Угроза убийством или причинением тяжкого вреда...   
43   Угроза убийством или причинением тяжкого вреда...   
44   Принуждение к изъятию органов или тканей челов...   
45   Принуждение к изъятию органов или тканей челов...   
46                     Заражение венерической болезнью   
47   Принуждение к изъятию органов или тканей челов...   
48   Заведомое поставление лица в опасность заражен...   
49                Заражение другого лица ВИЧ-инфекцией   
50   Заражение  другого лица ВИЧ-инфекцией, знавшим...   
51   Заражение ВИЧ-инфекцией вследствие ненадлежаще...   
52   Производство аборта лицом, не имеющим соответс...   
53   Производство аборта лицом, не имеющим соответс...   
54   Производство аборта лицом, не имеющим соответс...   
55                          Неоказание помощи больному   
56   Неоказание помощи больному, повлекшее по неост...   
57   Воспрепятствование в какой бы то ни было форме...   
58   Воспрепятствование в какой бы то ни было форме...   
59                              Оставление в опасности   
61                                  Похищение человека   
62   Похищение человека при отягчающих обстоятельствах   
63   Похищение человека при особо отягчающих обстоя...   
64                          Незаконное лишение свободы   
65   Незаконное лишение свободы при отягчающих обст...   
66   Незаконное лишение свободы при особо отягчающи...   
67                                     Торговля людьми   
68   Торговля людьми, совершенная при отягчающих об...   
69   Деяния, предусмотренные частями первой или вто...  

In [13]:
addDF = cleanClauseCol(addDF)
addDF = clauses2column(addDF)

firstCols = ['name', 'clause', 'part', 'totalConvictedMain']
addDF = rearrangeCols(addDF, firstCols)

addDF = addMilitaryOfences(addDF)
addDF['name'] = addDF['name'].str.replace('^\s{1}', '')
addDF['name'] = addDF['name'].str.replace('\n', '') 
addDF = sortTable(addDF)

<a id='data_check'></a>

### Проверка корректности обработки данных

Теперь нужно соединить все три таблицы за год в одну, но сначала проведем несколько проверок.

1) все три таблицы должны быть одной длины.

In [14]:
checkTablesLen(mainDF, addDF, parametersDF)
checkTablesLen(mainDF, addDF)

ОК: длины таблиц № 10.3 и № 10.3.1 совпадают
ОК: длины таблиц № 10.3 и № 10-а совпадают
ОК: длины таблиц № 10.3 и № 10-а совпадают


2) номера статей при построчном сравнении должны совпадать. Однако простое построчное сравнение может нас обмануть.В отчетных формах Судебного департамента могут соседствовать актуальная и утратившая силу части одной и той же статьи с одинаковыми номерами, при этом все примечания к номерам статей мы убрали, оставив их у названий статей/частей. Поэтому построчно имеет смысл сравнивать не только колонку с номерами статей, но и числа в тех столбцах, которые в разных формах должны содержать одинаковую информацию.


Так в форме № 10.3 и № 10.3.1 должны совпадать соответственно колонки "Лишение свободы" и сумма чисел из колонок "До 1 года вкл.", "Свыше 1 до 2 лет вкл.",	"Свыше 2 до 3 лет вкл.", "Свыше 3 до 5 лет вкл.", "Свыше 5 до 8 лет вкл.", "Свыше 8 до 10 лет вкл.", "Свыше 10 до 15 лет вкл.", "Свыше 15 до 20 лет вкл.".

А в формах № 10.3 и № 10-а - колонки "ВСЕГО ОСУЖДЕНО ЛИЦ" и "Число осужденных лиц по основной статье".

На практике так происходит не всегда и числа регулярно расходятся, поэтому приходится ориентироваться не на их полное совпадение, а на величину разницы между ними.

In [15]:
checkNumbersBetweenForms(year, mainDF, addDF, parametersDF)

Не совпадает число осужденных по основной статье. 
Статья:  Воинские преступления 
10.3: 979 
10-a: nan 
Год: 2020


Теперь можно свести все таблицы за один год в одну, удалив дублирующиеся столбцы, а именно столбцы с номером и частью статьи в формах № 10.3.1 и № 10-а и столбцы с числом осужденных по основному составу преступления в форме № 10-а.

In [16]:
addDF = addDF.drop(['clause', 'part', 'totalConvictedMain'], axis=1)
parametersDF = parametersDF.drop(['clause', 'part'], axis=1)
df = pd.concat([mainDF, parametersDF, addDF], axis=1)

firstCols = ['name', 'clause', 'part', 'totalConvicted']
df = rearrangeCols(df, firstCols)

In [17]:
df.head()

name clause    part  \
0                                         Убийство    105  105ч.1   
1          Убийство при отягчающих обстоятельствах    105  105ч.2   
2          Убийство матерью новорожденного ребенка    106     106   
3        Убийство, совершенное в состоянии аффекта    107  107ч.1   
4  Убийство в состоянии аффекта двух или более лиц    107  107ч.2   

   totalConvicted  primaryLifeSentence  primaryImprisonment  primarySuspended  \
0            4027                    0                 3993                27   
1             987                   34                  951                 1   
2              29                    0                   11                 9   
3              37                    0                    0                 1   
4               1                    0                    1                 0   

   primaryMilitaryDisciplinaryUnit  primaryArrest  primaryRestrain  \
0                                0              0                0   
1                                0              0                0   
2                                0              0                9   
3                                0              0               25   
4                                0              0                0   

   primaryRestrictionsInMilitaryService  primaryCorrectionalLabour  \
0                                     0                          0   
1                                     0                          0   
2                                     0                          0   
3                                     0                          6   
4                                     0                          0   

   primaryCommunityService  primaryForcedLabour  primaryDisqualification  \
0                        0                    0                        0   
1                        0                    0                        0   
2                        0                    0                        0   
3                        0                    1                        0   
4                        0                    0                        0   

   primaryFine  primaryOther  exemptionTimeServedFromImprisonment  \
0            0             0                                    0   
1            0             0                                    0   
2            0             0                                    0   
3            0             1                                    0   
4            0             0                                    0   

   exemptionTimeServedOther  exemptionAmnestyFromImprisonment  \
0                         1                                 0   
1                         0                                 0   
2                         0                                 0   
3                         2                                 0   
4                         0                                 0   

   exemptionAmnestyOther  exemptionOtherGroundsFromImprisonment  \
0                      0                                      6   
1                      0                                      1   
2                      0                                      0   
3                      0                                      0   
4                      0                                      0   

   exemptionOtherGroundsOther  acquittal  dismissalAbsenceOfEvent  ...  \
0                           0         23                        1  ...   
1                           0         18                        2  ...   
2                           0          0                        0  ...   
3                           1          0                        0  ...   
4                           0          0                        0  ...   

   primaryFine25_100  primaryFine100_300  primaryFine300_500  \
0                  0                   0                   0   
1                  0                   0                   0   

И привести таблицу в длинную форму.

In [18]:
dfMelted = meltTable(df, year)

In [19]:
dfMelted.head(20)

year clause      part                                               name  \
0   2020    105    105ч.1                                           Убийство   
1   2020    105    105ч.2            Убийство при отягчающих обстоятельствах   
2   2020    106       106            Убийство матерью новорожденного ребенка   
3   2020    107    107ч.1          Убийство, совершенное в состоянии аффекта   
4   2020    107    107ч.2    Убийство в состоянии аффекта двух или более лиц   
5   2020    108    108ч.1  Убийство при превышении пределов необходимой о...   
6   2020    108    108ч.2  Убийство при превышении мер, необходимых для з...   
7   2020    109    109ч.1                Причинение смерти по неосторожности   
8   2020    109    109ч.2  Причинение смерти по неосторожности при отягча...   
9   2020    109    109ч.3  Причинение смерти по неосторожности двум или б...   
10  2020  110.1  110.1ч.1  Склонение к совершению самоубийства или содейс...   
11  2020  110.1  110.1ч.2        Содействие совершению самоубийства советами   
12  2020  110.1  110.1ч.3  Деяния, предусмотренные частями первой или вто...   
13  2020  110.1  110.1ч.4  Деяния, предусмотренные частью первой или втор...   
14  2020  110.1  110.1ч.5  Деяния, предусмотренные частями первой или вто...   
15  2020  110.1  110.1ч.6  Деяния, предусмотренные частями первой, второй...   
16  2020  110.2  110.2ч.1  Организация деятельности, направленной на побу...   
17  2020  110.2  110.2ч.2  Организация деятельности, направленной на побу...   
18  2020    110    110ч.1                          Доведение до самоубийства   
19  2020    110    110ч.2  Доведение до самоубийства, совершенное при отя...   

         parameter value  
0   totalConvicted  4027  
1   totalConvicted   987  
2   totalConvicted    29  
3   totalConvicted    37  
4   totalConvicted     1  
5   totalConvicted   227  
6   totalConvicted     0  
7   totalConvicted   772  
8   totalConvicted   114  
9   totalConvicted    39  
10  totalConvicted     0  
11  totalConvicted     0  
12  totalConvicted     1  
13  totalConvicted     1  
14  totalConvicted     0  
15  totalConvicted     0  
16  totalConvicted     0  
17  totalConvicted     0  
18  totalConvicted     5  
19  totalConvicted     1

In [20]:
dfMelted.to_pickle('2020.pkl')